In [ ]:
# ..... build coexp network with pseudobulk exp data ..... #

In [2]:
library(dplyr)

In [3]:
## create coexpression network ## 
build_coexp_network <- function(net, method = "spearman", flag = "rank"){
    
    # Calculate correlation coefficients
    genes = rownames(net)
    net = net[rowSums(net) > 0, ]

#     print(paste0("... ",dim(net)[1]," of ",length(genes), " genes have non-zero expression" ))

    net = cor(t(net), method = method)
    
    # Create network
    temp = net[upper.tri(net, diag = T)]
    if (flag == "abs"){
        temp = abs(temp)
    }
    
#     print("...ranking")
    temp = rank(temp, ties.method = "average")  

#     print("...reconstructing matrix")
    net[upper.tri(net, diag = T)] = temp

    net = t(net)
    net[upper.tri(net, diag = T)] = temp

    net = net / max(net, na.rm = T)
    med = median(net, na.rm = T)

    ind = setdiff(genes, rownames(net))   # which genes are missing?

    temp = matrix(med, length(ind), dim(net)[2])
    rownames(temp) = ind

    net = rbind(net, temp)
    temp = matrix(med, dim(net)[1], length(ind))
    colnames(temp) = ind
    net = cbind(net, temp)

    # reorder to original
    net = net[genes, genes]
    diag(net) = 1

    return(net)
}

In [14]:
# Donor  TOF DCM  HCM  HF_HLHS  Neo_HLHS   
cond = 'Neo_HLHS'
load(paste0('CHD_', cond, '_pseudobulk_expression_matrices.Rdata'))
scbulk[1:2,]

CM       Neurons  Mac     Tcells Mast Endo      ENDOC LEC PeriC   
RP11-34P13.7 0.866133 0.000000 0.00000 0      0    0.5627882 0     0   0.000000
AL627309.1   2.482398 4.547522 8.29014 0      0    0.5409359 0     0   4.391744
             SMC EpiL CF       
RP11-34P13.7 0   0    0.7479063
AL627309.1   0   0    0.4206293

In [15]:
# correlate across all subclasses
options(warn = -1)
cor1 = build_coexp_network(scbulk, method = 'spearman')
dim(cor1)
cor1[1:3,1:3]

# save
fileo = paste0('CHD_', cond, '_coexp_net.Rdata')
save(cor1, file = fileo)

[1] 29266 29266

RP11-34P13.7 AL627309.1 AP006222.2
RP11-34P13.7 1.0000000    0.5216102  0.8112744 
AL627309.1   0.5216102    1.0000000  0.7571814 
AP006222.2   0.8112744    0.7571814  1.0000000